In [1]:
from config import POSTGRES_CONNECTION_STRING
import pandas as pd
from sqlalchemy import create_engine
import plotly.express as px
import random
from IPython.display import clear_output

In [2]:
MAPBOX_TOKEN = 'pk.eyJ1IjoicmVzaXZhbGV4IiwiYSI6ImNrdGxvbzgxaTBpcjIydm1qeGVxeXN5YTUifQ.hcWyP3yOX2jg0NHiTjg9Fg'
px.set_mapbox_access_token(MAPBOX_TOKEN)

In [3]:
def con():
    return create_engine(POSTGRES_CONNECTION_STRING)

In [4]:
objects = pd.read_sql_query('''
    select *
    from objects
''', con())

In [5]:
objects.shape

(13169, 6)

In [6]:
ids = objects.sample(len(objects) // 2)['id']

In [7]:
len(ids)

6584

In [8]:
LAT = 55.753220
LNG = 37.622513
DT_LAT = 0.15
DT_LNG = 0.25

In [9]:
def random_delta():
    return (random.random() - 0.5) * 2.0

In [10]:
coords = []
for id in ids:
    while True:
        rdt1 = random_delta()
        rdt2 = random_delta()
        if rdt1 * rdt1 + rdt2 * rdt2 < 1:
            break
    lat = LAT + rdt1 * DT_LAT
    lng = LNG + rdt2 * DT_LNG
    coords.append((id, lat, lng))
coords_df = pd.DataFrame(coords, columns=['id', 'lat', 'lng'])
coords_df.head()

id        lat        lng
0  100551  55.693610  37.719100
1  118404  55.640971  37.684076
2  121870  55.770484  37.654998
3  101209  55.774672  37.706269
4  117276  55.889656  37.665343

In [11]:
def update_object_coordinates(df):
    cn = con()
    for i, (_, row) in enumerate(df.iterrows()):
        clear_output(True)
        print(i)
        id = row['id']
        lat = row['lat']
        lng = row['lng']
        cn.execute('''
            update objects
            set lat = %(lat)s,
                lng = %(lng)s
            where id = %(id)s
        ''', {'lat': lat, 'lng': lng, 'id': id})

In [12]:
# update_object_coordinates(coords_df)

In [13]:
coord_objects = pd.read_sql_query('''
    select *
    from objects
''', con())
coord_objects.head()

id                                               name  department_id  \
0  120116    Спортивный комплекс образовательного учреждения       219814.0   
1  120117    Спортивный комплекс образовательного учреждения       219814.0   
2  120118  Спортивный комплекс дошкольного образовательно...       219814.0   
3  120119  Спортивный комплекс дошкольного образовательно...       219814.0   
4  120120    Спортивный комплекс образовательного учреждения       219814.0   

   proximity_id        lat        lng  
0           4.0  55.506423  37.582619  
1           4.0  55.734218  37.677645  
2           4.0  55.736673  37.682825  
3           4.0  55.732991  37.680191  
4           4.0  55.735142  37.684851

In [21]:
map_objects = coord_objects.copy()
fig = px.scatter_mapbox(map_objects, lat='lat', lon='lng', text='name', zoom=7, height=1000)
fig.update_layout(
    mapbox = {
        'zoom': 7},
    showlegend = False)
fig.show()